This code is supposed to perform an average resource allocation bipartite projection
For reference please read the book. The projection is going to be made **onto hosts**, because we found that doing it on parasites poses problems with a) similarity b) creating an answerable hypothesis.

Why do we use the average resource allocation to discount both for saturation problem and bandwidth problem.
Bandwidth problem: when there is a very rare parasites, which feeds upon only these two animals there is an argument that these animals are more similar that animals sharing a parasite which feeds upon 1000 other species.
Saturation problem: when these animals share 60% and 80% percent of parasites, there is an argument that these animals are more similar than animals sharing only 20% and 10% of animals.

Why do we use average, not minimum or maximum?
- minimum would mean taking the weight of directed link from the animal with lower share, maximum with greater. Minimum means that we can safely assume that both of them are ???? TO do - 
- average - ok, fine.
I think taking the minimum could make sense because it guarantees that both species are similar of at least this bar to each other.
But for now we go with average



In [3]:

import networkx as nx
import numpy as np
import pandas as pd
import pickle

In [128]:
df = pd.read_csv('./full_data.csv')
df.columns

Index(['Unnamed: 0.1', 'Unnamed: 0', 'Host', 'Parasite', 'ParasiteFull',
       'group', 'locality', 'hostgroup', 'animal_nodes', 'parasites_nodes'],
      dtype='object')

Below I'm assigning every property to the host, such that after projection we loose no data.
Remember:
- animalis might be victims of multiple paragroups
- animals are assigned to one hostgroup.
- animals might be in multiple localities.
- parasites are assigned to one hostgroup and one paragroup and multiple localities

In [129]:
# Initialize graph
G = nx.Graph()

# Create a mapping from names (parasites/hosts) to unique integers
label_to_id = {}
counter = 0

for i, el in df.iterrows():
    # If the parasite is not yet in the mapping, assign it a unique number
    if el['Parasite'] not in label_to_id:
        label_to_id[el['Parasite']] = counter
        counter += 1

    # If the host is not yet in the mapping, assign it a unique number
    if el['Host'] not in label_to_id:
        label_to_id[el['Host']] = counter
        counter += 1

    # Get the numeric IDs for the parasite and host
    parasite_id = label_to_id[el['Parasite']]
    host_id = label_to_id[el['Host']]

    # Add the Parasite node with its attributes (numeric ID)
    if not G.has_node(parasite_id):
        para_group = set()
        para_group.add(el['group'])
        locality = set()
        locality.add(el['locality'])
        host_groups = set()
        host_groups.add(el['hostgroup'])
        G.add_node(parasite_id, bipartite=0, para_group=para_group, locality=locality, host_groups=host_groups)
    else:
        G.nodes[parasite_id]['locality'].add(el['locality'])
        G.nodes[parasite_id]['para_group'].add(el['group'])
        G.nodes[parasite_id]['host_groups'].add(el['hostgroup'])

    # Add the Host node with its attributes (numeric ID)
    if not G.has_node(host_id):
        G.add_node(host_id, bipartite=1, host_group=el['hostgroup'])

    # Add edge between Parasite and Host (numeric IDs)
    if not G.has_edge(parasite_id, host_id):
        G.add_edge(parasite_id, host_id)


In [130]:
# average resource allocation bipartite projection for host nodes
# ProbS you multiply the stochastic with a stochastic version of the transpose. then get (wu,v + wv,u)/2
# code below:

bipartite_one_nodes = [ n for n, d in G.nodes(data=True) if d.get('bipartite') == 0]
print(len(bipartite_one_nodes))
badj = nx.bipartite.biadjacency_matrix(G, row_order=sorted(bipartite_one_nodes)).toarray()

14720


In [131]:
# row stochastic adjacency matrix, of going from host to parasite
A = badj / badj.sum(axis=1)[:, np.newaxis]
At = badj.T / badj.T.sum(axis=1)[:, np.newaxis]
weights = A @ At

In [132]:
# now we have directional weights, we need to get the average
resource_allocation_weights = (weights + weights.T) / 2
# sanity check: symmetric matrix
print(np.allclose(resource_allocation_weights, resource_allocation_weights.T))
# compute the number of edges
print(np.count_nonzero(~np.isclose(resource_allocation_weights,0)) / 2)


True
536221.0


In [133]:
sum(resource_allocation_weights[1, :])

2.995043722843138

SELF LOOPS, are we care about them? not much tbh, we can remove them later.
We don't care - we need to remove them later.

In [134]:

# are there any nans in resource_allocation_weights?
print(np.isnan(resource_allocation_weights).any())
# are there any inf in resource_allocation_weights?
print(np.isinf(resource_allocation_weights).any())
# are there any rows that sum to zero? (contains only zeros)
print(np.any(np.isclose(resource_allocation_weights.sum(axis=1), 0)))
# are there any rows which have only one non-zero element?
print(np.any(np.count_nonzero(resource_allocation_weights, axis=1) == 1))

# are there rows not summing to 1?
print(np.any(np.isclose(resource_allocation_weights.sum(axis=1), 1) == False))

False
False
False
True
True


In [135]:
# do the noise corrected disparity filter
# You don't need to take care of zeros, because these are going to be zero anyway after the filtering


node_edges_weights_sum = resource_allocation_weights.sum(axis=1)
edge_neighbourhood_weights_sums = node_edges_weights_sum[:, np.newaxis] - resource_allocation_weights
# are there rows that sum to zero? (contains only zeros)
print(np.any(np.isclose(edge_neighbourhood_weights_sums.sum(axis=1), 0)))

edge_neighbourhood_weights_means = edge_neighbourhood_weights_sums / (np.count_nonzero(resource_allocation_weights, axis=1) - 1)[:, np.newaxis]
# there could be 0/0, which would result in nan, replace these with zeros
# I don't understand how infs emerge, but they do, so replace them with zeros
edge_neighbourhood_weights_means = np.nan_to_num(edge_neighbourhood_weights_means, nan=0, posinf=0, neginf=0)

# above should not be symmetric
print(np.allclose(edge_neighbourhood_weights_means, edge_neighbourhood_weights_means.T))
disparity_filter = (edge_neighbourhood_weights_means + edge_neighbourhood_weights_means.T) / 2

# where the values are below the disparity filter, set to zero
filtered_weights = resource_allocation_weights.copy()
# check if both disparity filter and resource_allocation_weights are symmetric
print(np.allclose(disparity_filter, disparity_filter.T))
print(np.allclose(resource_allocation_weights, resource_allocation_weights.T))
filtered_weights[resource_allocation_weights < disparity_filter] = 0
filtered_weights

False


/var/folders/vw/nff8_41x38jcbpv0nvrcxv700000gn/T/ipykernel_30063/780204485.py:10: RuntimeWarning: divide by zero encountered in divide
  edge_neighbourhood_weights_means = edge_neighbourhood_weights_sums / (np.count_nonzero(resource_allocation_weights, axis=1) - 1)[:, np.newaxis]
/var/folders/vw/nff8_41x38jcbpv0nvrcxv700000gn/T/ipykernel_30063/780204485.py:10: RuntimeWarning: invalid value encountered in divide
  edge_neighbourhood_weights_means = edge_neighbourhood_weights_sums / (np.count_nonzero(resource_allocation_weights, axis=1) - 1)[:, np.newaxis]


False
True
True


array([[0.11708533, 0.01886026, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.01886026, 0.16140876, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.51851852, ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.        , 0.        , 0.        , ..., 0.05555556, 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.02857143,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.5       ]])

In [136]:
# check if the filtered weights are symmetric
print(np.allclose(filtered_weights, filtered_weights.T))
# compute the number of values which are not close to zero
print(np.count_nonzero(~np.isclose(filtered_weights, 0))/2)
filtered_weights.shape

True
190038.0


(14720, 14720)

Filtered weights is not symmetric, but has inconsistent amount of edges? :()

In [137]:
# filtered_weights is the updated weight matrix, assumed to be symmetric

n = filtered_weights.shape[0]

# Option 1: Clear all edges (optional, based on your need)
G.clear_edges()

# Find the indices of non-zero weights in the upper triangle (ignoring diagonal)
rows, cols = np.triu_indices(n, k=1)  # k=1 skips the diagonal
non_zero_indices = np.where(~np.isclose(filtered_weights[rows, cols], 0))

# Prepare edges and their weights as a list of tuples (u, v, weight)
edges_with_weights = [
    (rows[idx], cols[idx], filtered_weights[rows[idx], cols[idx]]) 
    for idx in non_zero_indices[0]
]

# Batch add all edges to the graph
G.add_weighted_edges_from(edges_with_weights)

# Optionally: Check the updated edges in the graph
print(G.edges(data=True))  # This will show the edges and their weights


[(0, 1, {'weight': 0.018860256663051692}), (0, 4, {'weight': 0.011708633146541643}), (0, 158, {'weight': 0.024285714285714285}), (0, 662, {'weight': 0.04120879120879121}), (0, 841, {'weight': 0.015029278775099682}), (0, 1191, {'weight': 0.01984126984126984}), (0, 1273, {'weight': 0.015590828924162256}), (0, 3992, {'weight': 0.008729431727797742}), (0, 4010, {'weight': 0.019059065934065932}), (0, 4558, {'weight': 0.02232142857142857}), (0, 4559, {'weight': 0.04120879120879121}), (0, 4601, {'weight': 0.021060584393917725}), (0, 4602, {'weight': 0.015434342105210452}), (0, 4607, {'weight': 0.015756302521008403}), (0, 4615, {'weight': 0.022144702325374598}), (0, 4630, {'weight': 0.012874158672478}), (0, 4670, {'weight': 0.014047619047619047}), (0, 9067, {'weight': 0.022298300520089232}), (0, 9097, {'weight': 0.016839288267859694}), (0, 9104, {'weight': 0.01433346065699007}), (0, 9128, {'weight': 0.011818719536249585}), (0, 9440, {'weight': 0.016531471616123124}), (0, 9660, {'weight': 0.008

In [138]:
# Save the graph to a file
with open('projected_plus_weight.gpickle', 'wb') as f:
    pickle.dump(G, f, protocol=pickle.HIGHEST_PROTOCOL)


In [7]:
# Load the graph from the file
with open('projected_plus_weight.gpickle', 'rb') as f:
    G = pickle.load(f)


# G_loaded.nodes() or G_loaded.edges()


In [5]:
G_loaded[0][1]['weight']

0.018860256663051692

In [9]:
import networkx as nx

# Assuming G is your graph and (u, v) are two nodes
# preds = nx.jaccard_coefficient(G, [(u, v)])

# Print the Jaccard coefficient
for u, v, p in preds:
    print(f"Jaccard coefficient between {u} and {v}: {p}")


NameError: name 'u' is not defined